# Setup

## Create legacy HVR

In [ ]:
import sys
import numpy as np
import matplotlib.pyplot as plt

sys.path.append("..")
import rasterizer
import raster_assistant as ra

sys.path.append('../triskele/python/')
import triskele

figsize = np.array((16, 3)) * 1.5

In [ ]:
data = ra.bulk_load('../Data/lidar/C3/', filter_treshold=0)

In [ ]:
raster = rasterizer.vhr(data.spatial, data.z, dtype=np.float32)

In [ ]:
plt.figure(figsize=figsize)
plt.imshow(raster)
plt.show()
plt.imsave('../Res/tmp.png', raster)

# Noise Profile

In [ ]:
plt.hist(data.z, bins=1000)
plt.show()

In [ ]:
plt.hist(data.intensity, bins=1000)
plt.show()

In [ ]:
plt.figure(figsize=(10,10))
plt.hist2d(data.intensity, data.z, bins=1000)
plt.show()

In [ ]:
treshold = .5
tresholds_i = np.percentile(data.intensity, [treshold, 100 - treshold])
tresholds_z = np.percentile(data.z, [treshold, 100 - treshold])

intensity_filter = np.logical_or(data.intensity < tresholds_i[0], data.intensity > tresholds_i[1])
z_filter = np.logical_or(data.z < tresholds_z[0], data.z > tresholds_z[1])
all_filter = np.logical_or(intensity_filter, z_filter)
inter_filter = np.logical_and(z_filter, intensity_filter)

data.x.size, intensity_filter.sum(), z_filter.sum(), all_filter.sum(), inter_filter.sum()

The z and intensity noise seems uncorrelated.

## Noise rasters

### Denoise altitude for voxels computation...

In [ ]:
Z = data.spatial[:,2]
ra.auto_filter(Z)
data.spatial = np.hstack((data.spatial[:,:2], Z.reshape(-1, 1)))

### Compute noise rasters

In [ ]:
all_noise = rasterizer.rasterize(data.spatial, all_filter.astype(np.float16), .5, 'nearest', dtype=np.float16)
z_noise = rasterizer.rasterize(data.spatial, z_filter.astype(np.float16), .5, 'nearest', dtype=np.float16)
i_noise = rasterizer.rasterize(data.spatial, intensity_filter.astype(np.float16), .5, 'nearest', dtype=np.float16)
inter_noise = rasterizer.rasterize(data.spatial, inter_filter.astype(np.float16), .5, 'nearest', dtype=np.float16)

### Display

In [ ]:
fig, axs = plt.subplots(4, figsize=figsize * 4)
for i, fig_title in enumerate(zip((all_noise, z_noise, i_noise, inter_noise), ('All', 'Altitude', 'Intensity', 'Intersection'))):
    axs[i].imshow(fig_title[0].astype(np.float32))
    axs[i].set_title(fig_title[1])
plt.show()

### Z and Int cutoff visualisation

In [ ]:
fig, axs = plt.subplots(2, 2, figsize=(200,200))
for ax, filter_title in zip(axs.flatten(), zip((all_filter, z_filter, intensity_filter, inter_filter), ('All', 'Altitude', 'Intensity', 'Intersection'))):
    ax.set_title(filter_title[1])
    ax.hist2d(data.intensity[np.logical_not(filter_title[0])], data.z[np.logical_not(filter_title[0])], bins=1000)
fig.tight_layout()
plt.show()

### Reconstruct denoised rasters

#### All filter

In [ ]:
raster_all = rasterizer.vhr(data.spatial[np.logical_not(all_filter)], data.z[np.logical_not(all_filter)], dtype=np.float32)

In [ ]:
plt.figure(figsize=figsize)
plt.imshow(raster_all)
plt.show()
plt.imsave('../Res/tmp_all.png', raster_all)

#### Intensity filter

In [ ]:
raster_i = rasterizer.vhr(data.spatial[np.logical_not(intensity_filter)], data.z[np.logical_not(intensity_filter)], dtype=np.float32)

In [ ]:
plt.figure(figsize=figsize)
plt.imshow(raster_i)
plt.show()
plt.imsave('../Res/tmp_i.png', raster_i)

#### Z filter

In [ ]:
raster_z = rasterizer.vhr(data.spatial[np.logical_not(z_filter)], data.z[np.logical_not(z_filter)], dtype=np.float32)

In [ ]:
plt.figure(figsize=figsize)
plt.imshow(raster_z)
plt.show()
plt.imsave('../Res/tmp_z.png', raster_z)

# Extremum clipping

In [ ]:
def extremum_filter(data, treshold=.5):
    tresholds_i = np.percentile(data.intensity, [treshold, 100 - treshold])
    tresholds_z = np.percentile(data.z, [treshold, 100 - treshold])

    intensity_filter = np.logical_or(data.intensity < tresholds_i[0], data.intensity > tresholds_i[1])
    z_filter = np.logical_or(data.z < tresholds_z[0], data.z > tresholds_z[1])
    all_filter = np.logical_or(intensity_filter, z_filter)
    #inter_filter = np.logical_and(z_filter, intensity_filter)

    return all_filter

In [ ]:
tresholds = (0., .1, .2, .5, 1.)

fig, axs = plt.subplots(len(tresholds), figsize=figsize * len(tresholds))

for ax, t in zip(axs, tresholds):
    f = extremum_filter(data, t)
    raster = rasterizer.vhr(data.spatial[np.logical_not(f)], data.z[np.logical_not(f)], dtype=np.float32)
    ax.imshow(raster)
    ax.set_title(str(t))
    plt.imsave('../Res/extremum_clip_z_{}.png'.format(t), raster)
plt.show()
    

0.1 % seems optimal.

### Reproductivity

In [ ]:
data2 = ra.bulk_load('../Data/lidar/C1/', filter_treshold=0)

In [ ]:
tresholds = (0., .1, .2, .5, 1.)

fig, axs = plt.subplots(len(tresholds), figsize=figsize * len(tresholds))

for ax, t in zip(axs, tresholds):
    f = extremum_filter(data2, t)
    raster = rasterizer.vhr(data2.spatial[np.logical_not(f)], data2.z[np.logical_not(f)], dtype=np.float32)
    ax.imshow(raster)
    ax.set_title(str(t))
    plt.imsave('../Res/extremum_clip_z_{}.png'.format(t), raster)
plt.show()
    